<h1><span style = "color: blue; font-weight:bold" > Scrapping Covid Data from Ministry of Health</span></h1>

This notebook is to collect the covid situation which is happenning in Vietnam

<h2> 1. Import library</h2>

In [59]:
import pandas as pd
import numpy as np
import requests
import requests
from bs4 import BeautifulSoup
import lxml.html
import datetime
import time
import pandas as pd
import re
from tqdm import tqdm
from requests.adapters import HTTPAdapter
from requests.packages.urllib3.util.retry import Retry
import matplotlib.pyplot as plt
import seaborn as sns

<h2> 2. Scrapped Data </h2>

In [20]:
page = requests.get("https://ncov.moh.gov.vn/", verify = False)

/Users/NT/anaconda3/lib/python3.7/site-packages/urllib3/connectionpool.py:847: InsecureRequestWarning: Unverified HTTPS request is being made. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  InsecureRequestWarning)


In [22]:
soup = BeautifulSoup(page.text, 'html.parser')

In [24]:
soup.prettify()

'<!DOCTYPE html>\n<html class="ltr" dir="ltr" lang="vi-VN">\n <head>\n  <title>\n   TRANG TIN VỀ DỊCH BỆNH VIÊM ĐƯỜNG HÔ HẤP CẤP COVID-19 - Bộ Y tế - Trang tin về dịch bệnh viêm đường hô hấp cấp COVID-19\n  </title>\n  <meta content="initial-scale=1.0, width=device-width" name="viewport"/>\n  <meta content="text/html; charset=utf-8" http-equiv="content-type"/>\n  <meta content="TRANG TIN VỀ DỊCH BỆNH VIÊM ĐƯỜNG HÔ HẤP CẤP COVID-19" lang="vi-VN" name="robots"/>\n  <meta content="TRANG TIN VỀ DỊCH BỆNH VIÊM ĐƯỜNG HÔ HẤP CẤP COVID-19" lang="vi-VN" name="description"/>\n  <meta content="TRANG TIN VỀ DỊCH BỆNH VIÊM ĐƯỜNG HÔ HẤP CẤP COVID-19" lang="vi-VN" name="keywords"/>\n  <link data-senna-track="temporary" href="https://moh.gov.vn" rel="canonical"/>\n  <link data-senna-track="temporary" href="https://moh.gov.vn" hreflang="vi-VN" rel="alternate"/>\n  <link data-senna-track="temporary" href="https://moh.gov.vn/en" hreflang="en-US" rel="alternate"/>\n  <link data-senna-track="temporary" hre

<h2> 3. Extract & Clean data </h2>

In [162]:
soup1 = soup.find_all('table', attrs={"class":"table table-striped table-covid19", "id":"sailorTable"})

In [163]:
res = soup1[0].find_all('td')

In [164]:
def name_extract (result_list):
    data =pd.DataFrame()
    colnames = ['patient_number','age','province','status','nationality']
    for i in range (0,5):
        data.insert (i, colnames[i],[m.get_text() for m in result_list[i::5]])
    return data


In [175]:
data =name_extract(res)
data.head()

patient_number age   province         status nationality
0         BN4579  21  Bắc Giang  Đang điều trị    Việt Nam
1         BN4578  83  Bắc Giang  Đang điều trị    Việt Nam
2         BN4577  35  Bắc Giang  Đang điều trị    Việt Nam
3       BN4576\t  21  Bắc Giang  Đang điều trị    Việt Nam
4         BN4575  32  Bắc Giang  Đang điều trị    Việt Nam

In [170]:
data.patient_number =data.patient_number.apply(lambda x: x.replace("\t",""))

<h2> 4. Translate to English </h2>

In [171]:
import google_trans_new
from google_trans_new import google_translator  

Demo translate

In [172]:
translator = google_translator()  
print(translator.translate('Đang điều trị',lang_tgt='en'))

Being treated 


Loop to translate all rows in Vietnamese to English

In [173]:
translator = google_translator()
translations = {}
for column in data.columns[2:5]:
    # Unique elements of the column
    unique_elements = data[column].unique()
    for element in unique_elements:
        # Adding all the translations to a dictionary (translations)
        translations[element] = translator.translate(element,lang_tgt='en')


In [174]:
translations

{'Bắc Giang': 'Bac Giang ',
 'Hà Nội': 'Hanoi ',
 'Vĩnh Phúc': 'Vinh Phuc ',
 'Bắc Ninh': 'Bac Ninh ',
 'Thái Bình': 'peaceful ',
 'Điện Biên': 'Dien Bien ',
 'Hải Dương': 'Hai Duong ',
 'Lạng Sơn': 'Lang Son ',
 'Hồ Chí Minh': 'Ho Chi Minh ',
 'Hà Nam': 'Henan ',
 'Đà Nẵng': 'Danang ',
 'Hải Phòng': 'Hai Phong ',
 'Hưng Yên': 'hung Yen ',
 'Sơn La': 'Son La ',
 'Phú Thọ': 'Phu-Tho ',
 'Khánh Hòa': 'Khanh Hoa ',
 'Bà Rịa - Vũng Tàu': 'BA Ria Vung Tau ',
 'Tuyên Quang': 'Tuyen Quang ',
 'Hoà Bình': 'Peace ',
 'Nam Định': 'Nam Dinh ',
 'Quảng Ninh': 'Quang Ninh ',
 'Vĩnh Long': 'Vinh Long ',
 'Đắk Lắk': 'Dak Lak ',
 'Hà Giang': 'Ha Giang ',
 'Bình Dương': 'Binh Duong ',
 'Sóc Trăng': 'Soc Trang ',
 'Đồng Nai': 'Dong Nai ',
 'Thừa Thiên Huế': 'Hue ',
 'An Giang': 'An Giang ',
 'Long An': 'Long An ',
 'Quảng Trị': 'Quang Tri ',
 'Hà Tĩnh': 'Ha Tinh ',
 'Quảng Nam': 'Quang Nam ',
 'Tiền Giang': 'Tien Giang ',
 'Cần Thơ': 'Can Tho ',
 'Bình Thuận': 'Binh Thuan ',
 'Nghệ An': 'Nghe An ',
 'Th

In [193]:
adj_dic = {'Thái Bình': 'Thai Binh','Hà Nam': 'Ha Nam ','Hoà Bình': 'Hoa Binh ',
           'Gia Lai': 'Gia Lai','Bình Định': 'Binh Dinh','Khỏi': 'Recovered',
           'Áo': 'Austria','Đức': 'Germany', 'U-dơ-bê-ki-xtan': 'Uzbekistan',
           'Ba Lan': 'Poland','Nga': 'Russia','Bra-xin': 'Brazil','Li-bi': 'Libya',
           'Nê-pan': 'Nepal ','Hung-ga-ri': 'Hungary ','Pháp': 'France ','Mi-an-ma': 'Myanmar',
          'Lát-vi-a': 'Latvia', 'Moldova': 'Moldova', 'And Islands ':'Vietnam'}

In [194]:
for i in translations.keys():
    if i in adj_dic.keys():
        translations[i] = adj_dic[i]

In [202]:
data.replace(translations, inplace = True)

In [203]:
data.head()

patient_number age    province          status nationality
0         BN4579  21  Bac Giang   Being treated     Vietnam 
1         BN4578  83  Bac Giang   Being treated     Vietnam 
2         BN4577  35  Bac Giang   Being treated     Vietnam 
3       BN4576\t  21  Bac Giang   Being treated     Vietnam 
4         BN4575  32  Bac Giang   Being treated     Vietnam

<h2> 5. Basic EDA </h2>

This is to explore answers for these questions:
1. Number of cases by province and country
2. Number of cases by status


<b>1. Number of cases by province and country</b>

In [180]:
data.groupby('province').patient_number.count().sort_values(ascending = False)

province
Hai Duong           778
Danang              641
Bac Giang           554
Hanoi               525
Bac Ninh            365
Ho Chi Minh         275
Khanh Hoa           142
Quang Nam           121
BA Ria Vung Tau     113
Vinh Phuc           106
Quang Ninh           90
hung Yen             68
Thai Binh            59
Bac Lieu             52
Binh Duong           45
Ha Nam               42
Kien Giang           39
Tay Ninh             38
Ninh Binh            36
Can Tho              34
Dien Bien            34
Hoa Binh             33
Dong Nai             29
Dong Thap            28
Phu Yen              28
Gia Lai              27
Thanh Hoa            25
Lang Son             25
Nam Dinh             25
Ben tre              20
Vinh Long            14
Quang Tri            13
Soc Trang            13
Ninh Thuan           12
Ha Tinh              12
Hai Phong            11
Binh Thuan           11
Long An              10
An Giang              9
Quang Ngai            8
Tra Vinh              8
Ca Mau 

In [217]:
data.groupby('nationality').patient_number.count().sort_values(ascending = False)

nationality
Vietnam                         4354
India                             54
Russia                            26
UK                                22
China                             12
USA                               12
Philippines                       11
South Africa                       8
Brazil                             7
France                             7
Germany                            6
Japan                              5
Taiwan                             5
Austria                            4
Korea                              4
Turkey                             3
Costa Rica Republic                3
Belarus                            3
Pakistan                           2
Ukraine                            2
Israel                             2
Vietnam                            2
Myanmar                            2
Canada                             1
Australia                          1
Uzbekistan                         1
Algeria                   

<b> 2. Number of cases by status </b>

In [219]:
data.groupby('status').patient_number.count()

status
Being treated     1851
Dead                37
Other                4
Recovered         2687
Name: patient_number, dtype: int64

In [223]:
data[data.status == 'Other ']

patient_number age province  status nationality
2350         BN2229  54   Hanoi   Other       Japan 
3815          BN764  67  Danang   Other     Vietnam 
4126          BN453  56  Danang   Other     Vietnam 
4161          BN418  61  Danang   Other     Vietnam

Status "Other" are used to refer to 4 patients that die because of other reason not covid
+ Patient 418: died because of chronic kidney disease ( 4 times negative test covid)
+ Patient 453: died because of chronic kidney disease, pneumonia, heart failure, stroke ( 3 times negative test covid)
+ Patient 764: died because of chronic kidney disease,hypertension, stroke ( 3 times negative test covid)
+ Patient 2229: died unknown reason ( 2 times negative test covid)